In [78]:
import psycopg2
import os
import sys
from psycopg2 import OperationalError, errorcodes, errors
import psycopg2.extras as extras

In [4]:
#import all necessary modules
import matplotlib.pyplot as plt
import pandas as pd
import numpy as np
import requests
import time
from pprint import pprint

# Import API key
import api_keys

# Get FBI API Key
API_KEY = api_keys.fbi_api_key

#Pull data from the website on trends for all crimes and all states from 2010 to 2019.

# base url for getting api data
base_url = "https://api.usa.gov/crime/fbi/sapi/"
#Create a list of states in order to request data from each state
stateAbbr = ['AL','AK','AZ','AR','CA','CO','CT','DE','FL','GA','HI','ID','IL','IN','IA','KS','KY','LA','ME','MD','MA','MI','MN','MS','MO','MT','NE','NV','NH','NJ','NM','NY','NC','ND','OH','OK','OR','PA','RI','SC','SD','TN','TX','UT','VT','VA','WA','WV','WI','WY']
#Create a list of variables that we want to explore data for. In this case male and females
variable = 'all'
#declare the start and end year for the time period that we want to look at
since = '2010'
until = '2019'

#create an empty dataframe
crime_data = pd.DataFrame(columns=[])

#Create a for loop to request data for each state and for each variable for the offense that we would like to look at.
for i in stateAbbr:
    desired_endpoint = "api/arrest/states/offense/" + i + '/' + variable + '/' + since + '/' + until
    req = requests.get(base_url + desired_endpoint+'?api_key='+API_KEY).json()
    new = pd.DataFrame(req["data"])
    #Create new columns in the dataframe so that we know what data corresponds to each state and variable.
    new['State'] = i
    #Append the data from each request to the dataframe
    crime_data = crime_data.append(new)

In [7]:
import itertools
#base url
base_url = "https://api.usa.gov/crime/fbi/sapi/"
#Create a list of states in order to request data from each state
stateAbbr = ['AL','AK','AZ','AR','CA','CO','CT','DE','FL','GA','HI','ID','IL','IN','IA','KS','KY','LA','ME','MD','MA','MI','MN','MS','MO','MT','NE','NV','NH','NJ','NM','NY','NC','ND','OH','OK','OR','PA','RI','SC','SD','TN','TX','UT','VT','VA','WA','WV','WI','WY']
offense = ["violent-crime", "property-crime"]
year = ['2010', "2011", "2012", "2013", "2014", "2015", "2016", "2017", "2018", '2019']

#create an empty dataframe
summarized_crime_type_data = pd.DataFrame(columns = [])

#Create a for loop to request data for each state and for each variable for the offense that we would like to look at.
for i,j,k in itertools.product(stateAbbr, offense, year):
    desired_endpoint = "api/summarized/state/" + i + "/" + j + "/" + k + "/" + k
    req = requests.get(base_url + desired_endpoint + "?api_key=" + API_KEY).json()
    new = pd.DataFrame(req["results"])
    #Create new columns in the dataframe so that we know what data corresponds to each state and variable.
    #new["State"] = i
    #new["Offense type"] = j
    #new["Year"] = k
    #Append the data from each request to the dataframe
    summarized_crime_type_data = summarized_crime_type_data.append(new)

In [8]:
summarized_crime_type_data.head()

ori  data_year        offense state_abbr  cleared  actual
0  AL0010000       2010  violent-crime         AL       26     349
1  AL0010100       2010  violent-crime         AL       53     289
2  AL0010200       2010  violent-crime         AL        0    1343
3  AL0010400       2010  violent-crime         AL       21     105
4  AL0010500       2010  violent-crime         AL       12      30

In [41]:
conn = psycopg2.connect("host=localhost dbname=postgres user=postgres password=CLS521")
cur = conn.cursor()
cur.execute('''CREATE TABLE Crime_Type
      (ori VARCHAR PRIMARY KEY,
      data_year INTEGER,
      offense VARCHAR,
      state_abbr CHAR(2),
      cleared INTEGER,
      actual INTEGER);''')
print("Table created successfully")

conn.commit()

DuplicateTable: relation "crime_type" already exists


In [90]:
param_dic = {
    "host"      : "localhost",
    "database"  : "postgres",
    "user"      : "postgres",
    "password"  : "CLS521"
}

def connect(param_dic):
    """ Connect to the PostgreSQL database server """
    conn = None
    try:
        # connect to the PostgreSQL server
        print('Connecting to the PostgreSQL database...')
        conn = psycopg2.connect(**param_dic)
    except (Exception, psycopg2.DatabaseError) as error:
        print(error)
        sys.exit(1) 
    return conn

def single_insert(conn, insert_req):
    """ Execute a single INSERT request """
    cursor = conn.cursor()
    try:
        cursor.execute(insert_req)
        conn.commit()
    except (Exception, psycopg2.DatabaseError) as error:
        print("Error: %s" % error)
        conn.rollback()
        cursor.close()
        return 1
    cursor.close()

# Connecting to the database
conn = connect(param_dic)
# Inserting each row
for i in summarized_crime_type_data.index:
    query = """
    INSERT into crime_type(column1, column2, column3, column4, column5, column6) values(%s,%s,%s,%s,%s,%s);
    """ % (summarized_crime_type_data['ori'], summarized_crime_type_data['data_year'], summarized_crime_type_data['offense'], summarized_crime_type_data['state_abbr'], summarized_crime_type_data['cleared'], summarized_crime_type_data['actual'])
    single_insert(conn, query)
# Close the connection
conn.close()

Connecting to the PostgreSQL database...
Error: syntax error at or near "AL0010000"
LINE 2: ..., column3, column4, column5, column6) values(0     AL0010000
                                                              ^

Error: syntax error at or near "AL0010000"
LINE 2: ..., column3, column4, column5, column6) values(0     AL0010000
                                                              ^

Error: syntax error at or near "AL0010000"
LINE 2: ..., column3, column4, column5, column6) values(0     AL0010000
                                                              ^

Error: syntax error at or near "AL0010000"
LINE 2: ..., column3, column4, column5, column6) values(0     AL0010000
                                                              ^

Error: syntax error at or near "AL0010000"
LINE 2: ..., column3, column4, column5, column6) values(0     AL0010000
                                                              ^

Error: syntax error at or near "AL0010000"
LINE 2: ..., col

Error: syntax error at or near "AL0010000"
LINE 2: ..., column3, column4, column5, column6) values(0     AL0010000
                                                              ^

Error: syntax error at or near "AL0010000"
LINE 2: ..., column3, column4, column5, column6) values(0     AL0010000
                                                              ^

Error: syntax error at or near "AL0010000"
LINE 2: ..., column3, column4, column5, column6) values(0     AL0010000
                                                              ^

Error: syntax error at or near "AL0010000"
LINE 2: ..., column3, column4, column5, column6) values(0     AL0010000
                                                              ^

Error: syntax error at or near "AL0010000"
LINE 2: ..., column3, column4, column5, column6) values(0     AL0010000
                                                              ^

Error: syntax error at or near "AL0010000"
LINE 2: ..., column3, column4, column5, column6) values(0

Error: syntax error at or near "AL0010000"
LINE 2: ..., column3, column4, column5, column6) values(0     AL0010000
                                                              ^

Error: syntax error at or near "AL0010000"
LINE 2: ..., column3, column4, column5, column6) values(0     AL0010000
                                                              ^

Error: syntax error at or near "AL0010000"
LINE 2: ..., column3, column4, column5, column6) values(0     AL0010000
                                                              ^

Error: syntax error at or near "AL0010000"
LINE 2: ..., column3, column4, column5, column6) values(0     AL0010000
                                                              ^

Error: syntax error at or near "AL0010000"
LINE 2: ..., column3, column4, column5, column6) values(0     AL0010000
                                                              ^

Error: syntax error at or near "AL0010000"
LINE 2: ..., column3, column4, column5, column6) values(0

Error: syntax error at or near "AL0010000"
LINE 2: ..., column3, column4, column5, column6) values(0     AL0010000
                                                              ^

Error: syntax error at or near "AL0010000"
LINE 2: ..., column3, column4, column5, column6) values(0     AL0010000
                                                              ^

Error: syntax error at or near "AL0010000"
LINE 2: ..., column3, column4, column5, column6) values(0     AL0010000
                                                              ^

Error: syntax error at or near "AL0010000"
LINE 2: ..., column3, column4, column5, column6) values(0     AL0010000
                                                              ^

Error: syntax error at or near "AL0010000"
LINE 2: ..., column3, column4, column5, column6) values(0     AL0010000
                                                              ^

Error: syntax error at or near "AL0010000"
LINE 2: ..., column3, column4, column5, column6) values(0

Error: syntax error at or near "AL0010000"
LINE 2: ..., column3, column4, column5, column6) values(0     AL0010000
                                                              ^

Error: syntax error at or near "AL0010000"
LINE 2: ..., column3, column4, column5, column6) values(0     AL0010000
                                                              ^

Error: syntax error at or near "AL0010000"
LINE 2: ..., column3, column4, column5, column6) values(0     AL0010000
                                                              ^

Error: syntax error at or near "AL0010000"
LINE 2: ..., column3, column4, column5, column6) values(0     AL0010000
                                                              ^

Error: syntax error at or near "AL0010000"
LINE 2: ..., column3, column4, column5, column6) values(0     AL0010000
                                                              ^

Error: syntax error at or near "AL0010000"
LINE 2: ..., column3, column4, column5, column6) values(0

...

Error: syntax error at or near "AL0010000"
LINE 2: ..., column3, column4, column5, column6) values(0     AL0010000
                                                              ^

Error: syntax error at or near "AL0010000"
LINE 2: ..., column3, column4, column5, column6) values(0     AL0010000
                                                              ^

Error: syntax error at or near "AL0010000"
LINE 2: ..., column3, column4, column5, column6) values(0     AL0010000
                                                              ^

Error: syntax error at or near "AL0010000"
LINE 2: ..., column3, column4, column5, column6) values(0     AL0010000
                                                              ^

Error: syntax error at or near "AL0010000"
LINE 2: ..., column3, column4, column5, column6) values(0     AL0010000
                                                              ^

Error: syntax error at or near "AL0010000"
LINE 2: ..., column3, column4, column5, column6) values(0

Error: syntax error at or near "AL0010000"
LINE 2: ..., column3, column4, column5, column6) values(0     AL0010000
                                                              ^

Error: syntax error at or near "AL0010000"
LINE 2: ..., column3, column4, column5, column6) values(0     AL0010000
                                                              ^

Error: syntax error at or near "AL0010000"
LINE 2: ..., column3, column4, column5, column6) values(0     AL0010000
                                                              ^

Error: syntax error at or near "AL0010000"
LINE 2: ..., column3, column4, column5, column6) values(0     AL0010000
                                                              ^

Error: syntax error at or near "AL0010000"
LINE 2: ..., column3, column4, column5, column6) values(0     AL0010000
                                                              ^

Error: syntax error at or near "AL0010000"
LINE 2: ..., column3, column4, column5, column6) values(0

Error: syntax error at or near "AL0010000"
LINE 2: ..., column3, column4, column5, column6) values(0     AL0010000
                                                              ^

Error: syntax error at or near "AL0010000"
LINE 2: ..., column3, column4, column5, column6) values(0     AL0010000
                                                              ^

Error: syntax error at or near "AL0010000"
LINE 2: ..., column3, column4, column5, column6) values(0     AL0010000
                                                              ^

Error: syntax error at or near "AL0010000"
LINE 2: ..., column3, column4, column5, column6) values(0     AL0010000
                                                              ^

Error: syntax error at or near "AL0010000"
LINE 2: ..., column3, column4, column5, column6) values(0     AL0010000
                                                              ^

Error: syntax error at or near "AL0010000"
LINE 2: ..., column3, column4, column5, column6) values(0

Error: syntax error at or near "AL0010000"
LINE 2: ..., column3, column4, column5, column6) values(0     AL0010000
                                                              ^

Error: syntax error at or near "AL0010000"
LINE 2: ..., column3, column4, column5, column6) values(0     AL0010000
                                                              ^

Error: syntax error at or near "AL0010000"
LINE 2: ..., column3, column4, column5, column6) values(0     AL0010000
                                                              ^

Error: syntax error at or near "AL0010000"
LINE 2: ..., column3, column4, column5, column6) values(0     AL0010000
                                                              ^

Error: syntax error at or near "AL0010000"
LINE 2: ..., column3, column4, column5, column6) values(0     AL0010000
                                                              ^

Error: syntax error at or near "AL0010000"
LINE 2: ..., column3, column4, column5, column6) values(0

Error: syntax error at or near "AL0010000"
LINE 2: ..., column3, column4, column5, column6) values(0     AL0010000
                                                              ^

Error: syntax error at or near "AL0010000"
LINE 2: ..., column3, column4, column5, column6) values(0     AL0010000
                                                              ^

Error: syntax error at or near "AL0010000"
LINE 2: ..., column3, column4, column5, column6) values(0     AL0010000
                                                              ^

Error: syntax error at or near "AL0010000"
LINE 2: ..., column3, column4, column5, column6) values(0     AL0010000
                                                              ^

Error: syntax error at or near "AL0010000"
LINE 2: ..., column3, column4, column5, column6) values(0     AL0010000
                                                              ^

Error: syntax error at or near "AL0010000"
LINE 2: ..., column3, column4, column5, column6) values(0